In [2]:
import re
import json
from collections import defaultdict
import difflib
import textwrap
import os

import sys
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import random
from typing import List, Tuple

from sklearn.model_selection import train_test_split
from transformers import AutoTokenizer
from typing import List, Dict
#from rapidfuzz import fuzz

# Predefined canonical names
target_names = [
    'Ellen Osborne', 'David Oberg', 'Graham Paige', 'Jonno Alcaro',
    'Katrina Callsen', 'Kate Acuff', 'Judy Le'
]

# Known aliases → canonical name
alias_map = {
    "Katherin Acuff": "Kate Acuff",
    "Katherine Acuff": "Kate Acuff",
    "Kate Acuff": "Kate Acuff",
    "Jonathan Alcaro": "Jonno Alcaro",
    "Jon Alcaro": "Jonno Alcaro",
    "Jonno Alcaro": "Jonno Alcaro"
}

clean_transcript_path = '/playpen-ssd/smerrill/dataset/cleantranscripts'
all_transcripts = os.listdir(clean_transcript_path)


### Make topics Json

In [6]:
output_json = {}
for transcript in all_transcripts:
    print(transcript)
    transcript_file = os.path.join(clean_transcript_path, transcript)
    text = np.load(transcript_file, allow_pickle=True)
    people_in_conversation = np.unique([x['speaker'] for x in text]).tolist()
    
    with open(f'/playpen-ssd/smerrill/dataset/topics/{transcript}.txt', 'r') as f:
        topics = f.readlines()
    topics = [x.split(':')[0].replace('**', '') for x in topics if x != '\n']
    output_json[transcript] = {'topics':topics,
                               'people': people_in_conversation}

output_path = "/playpen-ssd/smerrill/llm_decisions/configs/topics.json"

# Ensure the directory exists
os.makedirs(os.path.dirname(output_path), exist_ok=True)


# Save the dictionary as JSON
with open(output_path, "w", encoding="utf-8") as f:
    json.dump(output_json, f, indent=2)


8TdTe--0CUs.npy
hhvce_UUc4A.npy
o3f7y_9mHcE.npy
LUO7q6gjpvk.npy
MgHvV_9dxdA.npy
HbBO4irR6AA.npy
to9gvUa_6vM.npy
wyl3i48JFkA.npy
crHvtYkt7jA.npy
daLM5o6v67c.npy
6gwrzUFYMw8.npy
BQYLZNhIEDE.npy
NSizXN8dD5g.npy
PfwawD7a2Sg.npy
GarPnbypXRk.npy
xJvnLptI_SU.npy
_91XXbXeQD4.npy
9zIGFJbKhNg.npy
BFr19jzSYoM.npy
82YE6lBeZA8.npy
5YMkxWBgdtY.npy
xfVck0_Q84w.npy
zTstLGW-oOQ.npy
6WYXzne6dlY.npy
3BtZN2Tye08.npy
Bcl4e29n7m4.npy
qHxh7gmoY_I.npy
oSl6xiV1cSg.npy
5GglIIs8-B8.npy
b0dOdikDv0M.npy
cF4uYrMPQ24.npy
wbgxA2KNbiw.npy
rP7XyLqsAgc.npy
zLqFpa2i9Ow.npy
o-mxBguJmlU.npy
blaYeycF09Q.npy
5hxY73VZXok.npy
-A6v9Byfz20.npy


In [52]:
topics_file = '/playpen-ssd/smerrill/llm_decisions/configs/topics.json'
personas_file = '/playpen-ssd/smerrill/llm_decisions/configs/personas.json'
micro_profiles_file = '/playpen-ssd/smerrill/llm_decisions/configs/micro_profiles.json'


In [53]:
with open(topics_file, "r", encoding="utf-8") as f:
    topics_data = json.load(f)

with open(personas_file, "r", encoding="utf-8") as f:
    personas_data = json.load(f)

with open(micro_profiles_file, "r", encoding="utf-8") as f:
    micro_profiles_data = json.load(f)


In [54]:
micro_profiles_data

{'ellenosborne': {'avg_words_per_turn': 54.702127659574465,
  'longest_response_length': 730,
  'shortest_response_length': 5,
  'response_length_variance': 9759.071608327613,
  'question_freq': 0.35106382978723405,
  'hedging_rate': 0.14893617021276595,
  'directive_rate': 0.425531914893617,
  'politeness_rate': 0.06382978723404255},
 'grahampaige': {'avg_words_per_turn': 45.090825688073394,
  'longest_response_length': 736,
  'shortest_response_length': 3,
  'response_length_variance': 3829.2727348548033,
  'question_freq': 0.5963302752293578,
  'hedging_rate': 0.2908256880733945,
  'directive_rate': 0.3467889908256881,
  'politeness_rate': 0.463302752293578},
 'judyle': {'avg_words_per_turn': 66.4469696969697,
  'longest_response_length': 791,
  'shortest_response_length': 3,
  'response_length_variance': 9462.08082728425,
  'question_freq': 0.38257575757575757,
  'hedging_rate': 0.3446969696969697,
  'directive_rate': 0.44696969696969696,
  'politeness_rate': 0.24621212121212122},


In [55]:
def create_context_card(transcript_file, speaker):
    """
    Generate a structured, LLM-friendly context card for fine-tuning.
    
    Inputs:
        transcript_file: key/filename for transcript in topics_data
        speaker: the persona name
        
    Returns:
        context_card_text (str): formatted context card
    """
    
    # Extract data
    topics_list = topics_data[transcript_file]['topics']   # list of strings or paragraphs
    people_list = topics_data[transcript_file]['people']   # list of participant names
    persona_info = personas_data[speaker]                  # string describing tone, style, etc.
    micro_profile = micro_profiles_data[speaker]          # dict of numeric style stats
    style_tags = micro_profile.get('tags', [])            # optional descriptive tags
    
    # Format micro profile into bullets
    micro_lines = [
        f"- Avg Words per Turn: {micro_profile.get('avg_words_per_turn','N/A'):.2f}",
        f"- Longest Response: {micro_profile.get('longest_response_length','N/A')}",
        f"- Shortest Response: {micro_profile.get('shortest_response_length','N/A')}",
        f"- Response Variance: {micro_profile.get('response_length_variance','N/A'):.2f}",
        f"- Question Frequency: {micro_profile.get('question_freq','N/A')*100:.1f}%",
        f"- Hedging Rate: {micro_profile.get('hedging_rate','N/A')*100:.1f}%",
        f"- Directive Rate: {micro_profile.get('directive_rate','N/A')*100:.1f}%",
        f"- Politeness Rate: {micro_profile.get('politeness_rate','N/A')*100:.1f}%",
    ]
    
    # Add descriptive tags if available
    if style_tags:
        micro_lines.append(f"- Tags: {', '.join(style_tags)}")
    
    # Join micro lines and topics into strings
    micro_str = "\n        ".join(micro_lines)
    topics_str = "\n        ".join(topics_list)
    
    # Format people
    people_str = ", ".join(people_list)
    
    # Build the final context card string
    context_card = """
PROFILE:
Persona Name: {speaker}
Persona: {persona_info}
Micro Profile:
        {micro_str}

CONVERSATION CONTEXT:
Topics Discussed:
        {topics_str}
People in Conversation: {people_str}
""".format(
        speaker=speaker,
        persona_info=persona_info,
        micro_str=micro_str,
        topics_str=topics_str,
        people_str=people_str
    )
        
    return context_card.strip()


def create_context_card(transcript_file, speaker):
    """
    Generate a structured, LLM-friendly context card for fine-tuning.
    
    Inputs:
        transcript_file: key/filename for transcript in topics_data
        speaker: the persona name
        
    Returns:
        context_card_text (str): formatted context card
    """
    
    # Extract data
    topics_list = topics_data[transcript_file]['topics']   # list of strings or paragraphs
    people_list = topics_data[transcript_file]['people']   # list of participant names
    persona_info = personas_data[speaker]                  # string describing tone, style, etc.
    
    # Join topics into string
    topics_str = "\n        ".join(topics_list)
    
    # Format people
    people_str = ", ".join(people_list)
    
    # Build the final context card string (no micro profile)
    context_card = f"""
PROFILE:
Persona Name: {speaker}
Persona: {persona_info}

CONVERSATION CONTEXT:
Topics Discussed:
        {topics_str}
People in Conversation: {people_str}
""".strip()
        
    return context_card


In [56]:
personas_data

{'ellenosborne': 'Tone: Professional, clear, empathetic. Style: Evidence-based, inclusive, collaborative. Values: Equity, transparency, accountability. Leadership: Community-first, research-informed, reform-minded. Phrases: Grounded in research… In service of equity… Shared responsibility… To build trust…',
 'davidoberg': 'Tone: Formal, engaging, calm, with light humor. Style: Clear, fair, respectful, and constructive. Values: Fairness, equity, education, social justice. Leadership: Collaborative, open-minded, pragmatic idealist. Focus: Student well-being, especially vulnerable groups, and community growth. Phrases: With respect to history and context… Balancing idealism with pragmatism… Seeking common ground… Committed to fairness and inclusion…',
 'grahampaige': 'Tone: Warm, sincere, storytelling, empathetic. Style: Formal, structured, professional, appreciative. Values: Compassion, equity, respect, community connection. Leadership: Collaborative, inclusive, focused on eliminating sy

In [57]:
speaker = 'davidoberg'
all_transcripts

['MgHvV_9dxdA.npy',
 'GarPnbypXRk.npy',
 'oSl6xiV1cSg.npy',
 'crHvtYkt7jA.npy',
 'xJvnLptI_SU.npy',
 '6WYXzne6dlY.npy',
 'daLM5o6v67c.npy',
 'b0dOdikDv0M.npy',
 'BFr19jzSYoM.npy',
 'xfVck0_Q84w.npy',
 'blaYeycF09Q.npy',
 'o-mxBguJmlU.npy',
 'cF4uYrMPQ24.npy',
 '-A6v9Byfz20.npy',
 'rP7XyLqsAgc.npy',
 'PfwawD7a2Sg.npy',
 'wbgxA2KNbiw.npy',
 '8TdTe--0CUs.npy',
 '5YMkxWBgdtY.npy',
 'wyl3i48JFkA.npy',
 'to9gvUa_6vM.npy',
 'o3f7y_9mHcE.npy',
 'BQYLZNhIEDE.npy',
 'hhvce_UUc4A.npy',
 '82YE6lBeZA8.npy',
 '_91XXbXeQD4.npy',
 '6gwrzUFYMw8.npy',
 '9zIGFJbKhNg.npy',
 '5GglIIs8-B8.npy',
 '5hxY73VZXok.npy',
 'qHxh7gmoY_I.npy',
 'NSizXN8dD5g.npy',
 'Bcl4e29n7m4.npy',
 'LUO7q6gjpvk.npy',
 '3BtZN2Tye08.npy',
 'zTstLGW-oOQ.npy',
 'zLqFpa2i9Ow.npy',
 'HbBO4irR6AA.npy']

In [58]:
speaker = 'ellenosborne'
transcript = all_transcripts[0]
print(create_context_card(transcript, speaker))

PROFILE:
Persona Name: ellenosborne
Persona: Tone: Professional, clear, empathetic. Style: Evidence-based, inclusive, collaborative. Values: Equity, transparency, accountability. Leadership: Community-first, research-informed, reform-minded. Phrases: Grounded in research… In service of equity… Shared responsibility… To build trust…

CONVERSATION CONTEXT:
Topics Discussed:
        1. COVID-19 Response and Vaccination Efforts
        2. Scholarship and Educational Opportunities
        3. Virtual Learning and School Reopening
        4. Budget and Compensation Planning
        5. Education Foundation Proposal
People in Conversation: alnittheyhaas, angelplkey, attmonrhoos, clarakeiser, clarekelsar, cralggroup, davidoberg, eleengomez, ellenosborne, erinroyer, grahampaige, jamiegellner, jenniferjohnston, jonnoalcaro, judyle, kateacuff, katrinacallsen, kimberlylnk, lattnonvhaas, mathewhaas, matthewhaar, matthewhaas, mayahumaza, mayakumazawa, mayakumaze, mayakunaza, megangaspar, natthohaas, p

# Create dataset

In [59]:
# Shuffle the list to ensure randomness
random.seed(42)  # for reproducibility
random.shuffle(all_transcripts)

# Compute split index
split_idx = int(0.8 * len(all_transcripts))

# Split transcripts
train_transcripts = all_transcripts[:split_idx]
test_transcripts = all_transcripts[split_idx:]

print(f"Total transcripts: {len(all_transcripts)}")
print(f"Training transcripts: {len(train_transcripts)}")
print(f"Testing transcripts: {len(test_transcripts)}")


Total transcripts: 38
Training transcripts: 30
Testing transcripts: 8


In [114]:
import os
import numpy as np
import tiktoken

# Load LLaMA 3 compatible tokenizer once
enc = tiktoken.get_encoding("p50k_base")

def generate_examples(
    transcript_file: str,
    clean_transcript_path: str,
    target_speaker: str,
    context_tokens: int = 500,
    stride_tokens: int = 100
):
    """
    Generate chat-style fine-tuning examples from a single transcript.

    Args:
        transcript_file: filename of transcript (.npy)
        clean_transcript_path: folder containing transcript files
        target_speaker: speaker to create assistant examples for
        context_tokens: number of tokens for previous context
        stride_tokens: approximate tokens to advance per example

    Returns:
        examples: list of chat-style message lists
    """
    transcript_path = os.path.join(clean_transcript_path, transcript_file)
    transcript_data = np.load(transcript_path, allow_pickle=True)

    # Make sure create_context_card is defined
    context_card = create_context_card(transcript_file, target_speaker)

    examples = []

    # Build a line list with roles
    lines = []
    for entry in transcript_data:
        role = "assistant" if entry['speaker'] == target_speaker else "user"
        lines.append({"role": role, "speaker": entry['speaker'], "text": entry['text']})

    i = 0
    while i < len(lines):
        if lines[i]['role'] != 'assistant':
            i += 1
            continue  # only create examples for target speaker turns

        # Collect previous lines in reverse order until context_tokens reached
        prev_lines = []
        total_tokens = 0
        j = i - 1
        while j >= 0 and total_tokens < context_tokens:
            line_text = f"{lines[j]['speaker']}: {lines[j]['text']}"
            line_tokens = enc.encode(line_text)
            prev_lines.insert(0, {"role": lines[j]['role'], "content": line_text, "tokens": len(line_tokens)})
            total_tokens += len(line_tokens)
            j -= 1

        # Skip example if no previous context
        if not prev_lines:
            i += 1
            continue

        # Truncate earliest line if total_tokens > context_tokens
        if total_tokens > context_tokens and prev_lines:
            over_tokens = total_tokens - context_tokens
            first_line = prev_lines[0]
            tokens_line = enc.encode(first_line["content"])
            truncated_tokens = tokens_line[over_tokens:]
            truncated_text = enc.decode(truncated_tokens)
            speaker_name = first_line["content"].split(":")[0]
            role = first_line["role"]
            prev_lines[0] = {"role": role, "content": f"{speaker_name}:...{truncated_text}"}

        # Build chat-style messages
        messages = [{"role": "system", "content": context_card}]
        messages.extend([{"role": l["role"], "content": l["content"]} for l in prev_lines])
        # Prefix assistant content with speaker name
        messages.append({"role": "assistant", "content": f"{target_speaker}: {lines[i]['text']}"})

        examples.append(messages)

        # Advance index with rough stride
        i += 1
        while i < len(lines) and lines[i]['role'] != 'assistant':
            i += 1
        #i += stride_tokens // 10  # rough approximation, adjustable

    return examples


In [115]:
speakers

NameError: name 'speakers' is not defined

In [116]:
import json


agents=[
  'kateacuff',
  'ellenosborne',
  'grahampaige',
  'katrinacallsen',
  'davidoberg',
  'jonnoalcaro',
  'judyle'
]

dataset = {}
for speaker in agents:
    all_examples = []
    for tf in train_transcripts:
        all_examples.extend(generate_examples(tf, clean_transcript_path, speaker))
    dataset[speaker] = all_examples

output_path = '/playpen-ssd/smerrill/dataset'
# Save dataset to JSON file
with open(f"{output_path}/train_dataset.json", "w", encoding="utf-8") as f:
    json.dump(dataset, f, indent=2, ensure_ascii=False)
    
  
test_dataset = {}
for speaker in agents:
    all_examples = []
    for tf in test_transcripts:
        all_examples.extend(generate_examples(tf, clean_transcript_path, speaker))
    test_dataset[speaker] = all_examples

output_path = '/playpen-ssd/smerrill/dataset'
# Save dataset to JSON file
with open(f"{output_path}/test_dataset.json", "w", encoding="utf-8") as f:
    json.dump(test_dataset, f, indent=2, ensure_ascii=False)
    


In [ ]:
def get_dataset(train_path, test_path, speaker, sys_message=1):
    """
    Load train and test datasets from JSON files and return examples for a specific speaker.

    Args:
        train_path: path to the training dataset JSON file
        test_path: path to the testing dataset JSON file
        speaker: the persona name to filter examples

    Returns:
        train_examples: list of training examples for the specified speaker
        test_examples: list of testing examples for the specified speaker
    """
    with open(train_path, "r", encoding="utf-8") as f:
        train_dataset = json.load(f)
    
    with open(test_path, "r", encoding="utf-8") as f:
        test_dataset = json.load(f)
    
    train_examples = train_dataset.get(speaker, [])
    test_examples = test_dataset.get(speaker, [])
    
    if not sys_message:
        train_examples = [x[1:] for x in train_examples]
        test_examples = [x[1:] for x in test_examples]
    return train_examples, test_examples
    
    

In [135]:
train_examples, test_examples = get_dataset(train_path, test_path, speaker)

In [138]:
train_examples[0]

[{'role': 'system',
  'content': 'PROFILE:\nPersona Name: grahampaige\nPersona: Tone: Warm, sincere, storytelling, empathetic. Style: Formal, structured, professional, appreciative. Values: Compassion, equity, respect, community connection. Leadership: Collaborative, inclusive, focused on eliminating systemic barriers. Focus: Supporting all students, human connection, and systemic change. Phrases: Guided by compassion and equity… Honoring the dedication of educators… Working to eliminate barriers and opportunity gaps… Together, we build community and support every student…\n\nCONVERSATION CONTEXT:\nTopics Discussed:\n        1. COVID-19 and School Reopening Plans\n        2. Mental Health Concerns\n        3. Vaccination Efforts\n        4. Equity and Learning Models\n        5. Staffing and Accommodations\nPeople in Conversation: angelpilkey, bernardhairston, clarekeiser, davidoberg, debbiecollins, ebblecoll, ellenosborne, grahampaige, jeffvergales, jonnoalcaro, judyle, katrinacallsen

In [137]:
[x[1:] for x in train_examples]

[[{'role': 'assistant',
   'content': 'grahampaige: It is 6.30 and I called this special meeting February the 4th of the Albemarle County School Board back into order. Ms. Carlson, do you have a motion?'},
  {'role': 'user',
   'content': "katrinacallsen: I do.  I move that the board certify by recorded vote that to the best of each board member's knowledge, only public business matters lawfully exempted from the open meeting requirements of the Virginia Freedom of Information Act and identified in the motion authorizing the closed meeting were heard, discussed, or considered in the closed meeting."},
  {'role': 'assistant',
   'content': "grahampaige: It's been moved by Ms. Carlson, seconded by, was that Mr. Oberg? It was me, Graham. OK, Mr. Alcaro.  that we vote saying that nothing occurred in the closed session that was not covered in the initial motion. Maybe we'll take a roll call vote on this. So Ms."}],
 [{'role': 'assistant',
   'content': 'grahampaige: It is 6.30 and I called 

In [130]:
import pandas as pd
from transformers import AutoTokenizer

def compute_token_stats(train_path, test_path, agents, model_name="meta-llama/Meta-Llama-3-70B-Instruct"):
    # load tokenizer
    tokenizer = AutoTokenizer.from_pretrained(model_name, use_fast=True)

    def count_tokens(examples):
        total_context_tokens = 0
        total_content_tokens = 0
        for example in examples:
            for item in example:
                if item["role"] == "system":
                    continue
                tokens = tokenizer.encode(item["content"], add_special_tokens=False)
                if item["role"] == "assistant":
                    total_content_tokens += len(tokens)
                elif item["role"] == "user":
                    total_context_tokens += len(tokens)
        return total_context_tokens, total_content_tokens

    train_data = []
    test_data = []

    for speaker in agents:
        train_examples, test_examples = get_dataset(train_path, test_path, speaker)

        train_context, train_content = count_tokens(train_examples)
        test_context, test_content = count_tokens(test_examples)

        train_data.append({
            "speaker": speaker,
            "context_tokens": train_context,
            "content_tokens": train_content
        })
        test_data.append({
            "speaker": speaker,
            "context_tokens": test_context,
            "content_tokens": test_content
        })

    train_df = pd.DataFrame(train_data)
    test_df = pd.DataFrame(test_data)

    return train_df, test_df


In [131]:
train_df, test_df = compute_token_stats(train_path, test_path, agents)

In [132]:
train_df

speaker  context_tokens  content_tokens
0       kateacuff          128417           36057
1    ellenosborne           35178            5509
2     grahampaige          326740          133371
3  katrinacallsen          197329           83740
4      davidoberg           89394           22602
5     jonnoalcaro          147408           54263
6          judyle           84197           22088

In [84]:
test = train_examples[10]

In [ ]:
model_name = 'meta-llama/Meta-Llama-3-70B-Instruct'
tokenizer = AutoTokenizer.from_pretrained(model_name, use_fast=True)


In [95]:
train_examples = [tokenizer.apply_chat_template(x, tokenize=False) for x in train_examples]
train_data = Dataset.from_list([{"text": text} for text in train_examples])


In [96]:
train_data['text']

["<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nPROFILE:\nPersona Name: grahampaige\nPersona: Tone: Warm, sincere, storytelling, empathetic. Style: Formal, structured, professional, appreciative. Values: Compassion, equity, respect, community connection. Leadership: Collaborative, inclusive, focused on eliminating systemic barriers. Focus: Supporting all students, human connection, and systemic change. Phrases: Guided by compassion and equity… Honoring the dedication of educators… Working to eliminate barriers and opportunity gaps… Together, we build community and support every student…\n\nCONVERSATION CONTEXT:\nTopics Discussed:\n        1. COVID-19 and School Reopening Plans\n        2. Mental Health Concerns\n        3. Vaccination Efforts\n        4. Equity and Learning Models\n        5. Staffing and Accommodations\nPeople in Conversation: angelpilkey, bernardhairston, clarekeiser, davidoberg, debbiecollins, ebblecoll, ellenosborne, grahampaige, jeffvergales, jonn

In [46]:
test = tokenizer.apply_chat_template(all_examples[0],  tokenize=False)

In [48]:
print(test)

<|begin_of_text|><|start_header_id|>system<|end_header_id|>

PROFILE:
Persona Name: ellenosborne
Persona: Tone: Professional, clear, empathetic. Style: Evidence-based, inclusive, collaborative. Values: Equity, transparency, accountability. Leadership: Community-first, research-informed, reform-minded. Phrases: Grounded in research… In service of equity… Shared responsibility… To build trust…

CONVERSATION CONTEXT:
Topics Discussed:
        1. COVID-19 Response and Vaccination Efforts
        2. Scholarship and Educational Opportunities
        3. Virtual Learning and School Reopening
        4. Budget and Compensation Planning
        5. Education Foundation Proposal
People in Conversation: alnittheyhaas, angelplkey, attmonrhoos, clarakeiser, clarekelsar, cralggroup, davidoberg, eleengomez, ellenosborne, erinroyer, grahampaige, jamiegellner, jenniferjohnston, jonnoalcaro, judyle, kateacuff, katrinacallsen, kimberlylnk, lattnonvhaas, mathewhaas, matthewhaar, matthewhaas, mayahumaza, may

In [90]:
import sys
sys.path.append('/playpen-ssd/smerrill/llm_decisions')
from utils import train_test_split
train_data, eval_data, train_completion_data = train_test_split(
    'kateacuff'
)
from datasets import (Dataset, IterableDataset,)

train_data = Dataset.from_list([{"text": text} for text in train_data])


In [97]:
train_examples

["<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nPROFILE:\nPersona Name: grahampaige\nPersona: Tone: Warm, sincere, storytelling, empathetic. Style: Formal, structured, professional, appreciative. Values: Compassion, equity, respect, community connection. Leadership: Collaborative, inclusive, focused on eliminating systemic barriers. Focus: Supporting all students, human connection, and systemic change. Phrases: Guided by compassion and equity… Honoring the dedication of educators… Working to eliminate barriers and opportunity gaps… Together, we build community and support every student…\n\nCONVERSATION CONTEXT:\nTopics Discussed:\n        1. COVID-19 and School Reopening Plans\n        2. Mental Health Concerns\n        3. Vaccination Efforts\n        4. Equity and Learning Models\n        5. Staffing and Accommodations\nPeople in Conversation: angelpilkey, bernardhairston, clarekeiser, davidoberg, debbiecollins, ebblecoll, ellenosborne, grahampaige, jeffvergales, jonn